In [49]:
from __future__ import print_function
from IPython.display import display, HTML
import os
import sys
import csv
import time
import statistics
import numpy as np
import string
import re
import pandas as pd
import text_features_extractor as tfExtractor
from sklearn.model_selection import train_test_split
from sklearn.metrics import average_precision_score, accuracy_score, recall_score
#Keras
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential, model_from_json
from keras.layers import Dense, LSTM
from keras.layers import Flatten
from keras.layers.convolutional import Conv1D
from keras.layers.convolutional import MaxPooling1D
from keras.layers.embeddings import Embedding
from keras.preprocessing import sequence
from keras.utils import plot_model
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.pipeline import make_pipeline
from sklearn.pipeline import TransformerMixin
from sklearn.base import BaseEstimator
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import cross_val_score
from sklearn.externals import joblib
import tensorflow
from lime import lime_text
from lime.lime_text import LimeTextExplainer

In [50]:
#Read in the csv
engDataDf = pd.read_csv("data_with_features/eng_cleaned_data_f.csv", encoding='UTF-8')
#Only take the text and sentiment columns
engDataDf = engDataDf[['text', 'depressed']]
#Cleaning
"""
for index, row in engDataDf.iterrows():
    #Preprocessing
    chinText, engText = tfExtractor.splitChinEng(row['text'])
    text = tfExtractor.engPreprocessing(engText)
    engDataDf.set_value(index,'text',text)
"""
#Convert data to numpy array
X = np.array(engDataDf['text'].tolist())
Y = np.array(engDataDf['depressed'].tolist())
#Convert -1 label to 0
i = 0
for label in Y:
    if(label == -1):
        Y[i] = 0
    i += 1

In [51]:
xTrain, xTest, yTrain, yTest = train_test_split(X, Y, test_size=0.2, shuffle=True, random_state=42, stratify=Y)

In [52]:
vocabSize = 5000
maxLength = 17

In [53]:
class TextsToSequences(Tokenizer, BaseEstimator, TransformerMixin):
    """ Sklearn transformer to convert texts to indices list 
    (e.g. [["the cute cat"], ["the dog"]] -> [[1, 2, 3], [1, 4]])"""
    def __init__(self,  **kwargs):
        super().__init__(**kwargs)
        
    def fit(self, texts, y=None):
        self.fit_on_texts(texts)
        return self
    
    def transform(self, texts, y=None):
        return np.array(self.texts_to_sequences(texts))
        
sequencer = TextsToSequences(num_words=vocabSize)

In [54]:
class Padder(BaseEstimator, TransformerMixin):
    """ Pad and crop uneven lists to the same length. 
    Only the end of lists longernthan the maxlen attribute are
    kept, and lists shorter than maxlen are left-padded with zeros
    
    Attributes
    ----------
    maxlen: int
        sizes of sequences after padding
    max_index: int
        maximum index known by the Padder, if a higher index is met during 
        transform it is transformed to a 0
    """
    def __init__(self, maxlen=500):
        self.maxlen = maxlen
        self.max_index = None
        
    def fit(self, X, y=None):
        self.max_index = pad_sequences(X, maxlen=self.maxlen).max()
        return self
    
    def transform(self, X, y=None):
        X = pad_sequences(X, maxlen=self.maxlen)
        X[X > self.max_index] = 0
        return X

padder = Padder(maxLength)

In [55]:
def createCustomizedCnnModel():
    pass

In [71]:
batchSize = 50
maxFeatures = vocabSize + 1

def createCnnModel():
    #CNN model
    cnnModel = Sequential()
    cnnModel.add(Embedding(vocabSize, 128, input_length=maxLength))
    cnnModel.add(Conv1D(filters=128, kernel_size=3, padding='same', activation='relu'))
    cnnModel.add(MaxPooling1D(pool_size=2))
    cnnModel.add(Flatten())
    cnnModel.add(Dense(250, activation='relu'))
    cnnModel.add(Dense(1, activation='sigmoid'))
    cnnModel.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    #print(cnnModel.summary())
    return cnnModel

def createRnnModel():
    #CNN model
    rnnModel = Sequential()
    rnnModel.add(Embedding(5000, 128, input_length=maxLength))
    rnnModel.add(Conv1D(filters=128, kernel_size=3, padding='same', activation='relu'))
    rnnModel.add(MaxPooling1D(pool_size=2))
    rnnModel.add(LSTM(500, dropout=0.3, recurrent_dropout=0.3))
    rnnModel.add(Dense(1, activation='sigmoid'))
    rnnModel.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    print(rnnModel.summary())
    return rnnModel

# Use Keras Scikit-learn wrapper to instantiate a LSTM with all methods
# required by Scikit-learn for the last step of a Pipeline
"""
sklearnCnn = KerasClassifier(build_fn=createCnnModel, epochs=20, batch_size=batchSize, verbose=1)

# Build the Scikit-learn pipeline
engPreprocessPipeline = make_pipeline(sequencer, padder)
pipeline = make_pipeline(sequencer, padder, sklearnCnn)
engPreprocessPipeline.fit(xTrain, yTrain)
pipeline.fit(xTrain, yTrain);
"""

sklearnRnn = KerasClassifier(build_fn=createRnnModel, epochs=20, batch_size=batchSize, verbose=1)

# Build the Scikit-learn pipeline
"""
engPreprocessPipeline = make_pipeline(sequencer, padder)
pipeline = make_pipeline(sequencer, padder, sklearnRnn)
engPreprocessPipeline.fit(xTrain, yTrain)
pipeline.fit(xTrain, yTrain);
yPred = pipeline.predict(xTest)
yPredNorm = []
for p in yPred:
    if p > 0.5:
        yPredNorm.append(1)
    else:
        yPredNorm.append(0)
rnn_average_precision = average_precision_score(yTest, yPred)
rnn_recall_score = recall_score(yTest, yPred, average='binary')
rnn_accuracy_score = accuracy_score(yTest, yPredNorm)
print("Precision: " + str(rnn_average_precision))
print("Recall: " + str(rnn_recall_score))
print("Accuracy: " + str(rnn_accuracy_score))
"""

'\nengPreprocessPipeline = make_pipeline(sequencer, padder)\npipeline = make_pipeline(sequencer, padder, sklearnRnn)\nengPreprocessPipeline.fit(xTrain, yTrain)\npipeline.fit(xTrain, yTrain);\nyPred = pipeline.predict(xTest)\nyPredNorm = []\nfor p in yPred:\n    if p > 0.5:\n        yPredNorm.append(1)\n    else:\n        yPredNorm.append(0)\nrnn_average_precision = average_precision_score(yTest, yPred)\nrnn_recall_score = recall_score(yTest, yPred, average=\'binary\')\nrnn_accuracy_score = accuracy_score(yTest, yPredNorm)\nprint("Precision: " + str(rnn_average_precision))\nprint("Recall: " + str(rnn_recall_score))\nprint("Accuracy: " + str(rnn_accuracy_score))\n'

In [79]:
#Save preprocessing pipeline
joblib.dump(engPreprocessPipeline, "saved_model/engPreprocessPipeline.pkl")
print("pipeline saved")
engPreprocessPipeline = joblib.load('saved_model/engPreprocessPipeline.pkl')
print("pipeline loaded")

pipeline saved
pipeline loaded


#### Visualization

In [57]:
class_names = ['not_depressed', 'depressed']
explainer = LimeTextExplainer(class_names=class_names)
i = 0
j = 0
for testData in xTest:
    if(yTest[i] == 1):
        exp = explainer.explain_instance(testData, pipeline.predict_proba)
        print("Test text: " + testData)
        print('Probability(positive) =', pipeline.predict_proba([testData])[0,1])
        print('True class: %s' % class_names[yTest[i]])
        print(exp.as_list())
        exp.save_to_file("test_data_diagrams/tdd_" + str(j) + ".html")
        j += 1
        #exp.show_in_notebook(text=True)
    i += 1
"""
# We choose a sample from test set
idx = 36
testSample = xTest[idx]
exp = explainer.explain_instance(xTest[idx], pipeline.predict_proba)
print("Test text: " + testSample)
print('Probability(positive) =', pipeline.predict_proba([testSample])[0,1])
print('True class: %s' % class_names[yTest[idx]])
"""

C:\Users\richi\Anaconda3\envs\py3.5\lib\re.py:203: FutureWarning: split() requires a non-empty pattern match.
  return _compile(pattern, flags).split(string, maxsplit)


5000/5000 [==============================] - 0s     
Test text: RT charstarlene My heart goes out to those of us whose anxiety has gone from crippling to an accelerating vomit shit deathlike ever since 
1/1 [==============================] - 0s
Probability(positive) = 1.0
True class: depressed
[('anxiety', 0.093316885295179536), ('crippling', 0.082489095770610546), ('gone', 0.060789288746282692), ('deathlike', 0.053498166066265743), ('accelerating', 0.045214271739825292), ('us', 0.038486649193516791), ('those', -0.036995900552230496), ('vomit', 0.036033998558594779), ('out', -0.030753892863393601), ('heart', -0.025731840291756403)]
1/1 [==============================] - 0s
Probability(positive) = 0.999991
True class: depressed
[('depression', 0.69852727150009042), ('despair', 0.13807681895874635), ('https', -0.086145378584727733), ('co', 0.066219062729066774), ('darkthoughts', 0.018254716269248909), ('iMdQ9bUDgA', 0.0061564569286434575), ('t', -0.004989772828550231)]
1/1 [=============

1/1 [==============================] - 0s
Probability(positive) = 0.999998
True class: depressed
[('too', 0.14107065331475815), ('anxiety', 0.096921375158038753), ('crippling', 0.091735182627891626), ('not', -0.071784216186788888), ('way', 0.063657272802659107), ('successful', -0.06043847529889556), ('am', 0.048299991204508216), ('much', 0.036020413648153123), ('by', -0.035718684685030332), ('any', -0.025879774071737853)]
1/1 [==============================] - 0s
Probability(positive) = 0.973742
True class: depressed
[('depression', 0.89847754721781103), ('katie', 0.10467157710736395), ('having', -0.087671468813404846), ('dinner', -0.073003991086363212), ('are', -0.054811866182322325), ('for', -0.029480601415138179), ('what', 0.022360414170005265), ('you', 0.012553210659090186), ('and', -0.0099197773771660981), ('perrier', -0.0082456939017143405)]
1/1 [==============================] - 0s
Probability(positive) = 1.0
True class: depressed
[('depression', 0.076932790756855246), ('bipolar

5000/5000 [==============================] - 1s     
Test text: 22 I have a theory that people with anxiety make great TOs because we re all paranoid 
1/1 [==============================] - 0s
Probability(positive) = 0.992625
True class: depressed
[('anxiety', 0.56382823913953761), ('great', -0.36665323877085443), ('22', -0.20679394356691708), ('re', 0.16340743602738153), ('a', -0.12260539590503948), ('with', 0.097533907498314143), ('all', 0.093873649531093437), ('make', 0.093190068878721458), ('we', 0.087017265608465649), ('that', 0.046542696730176289)]
1/1 [==============================] - 0s
Probability(positive) = 0.999997
True class: depressed
[('hvPac4', 0.47557661241257226), ('now', -0.26634467485940289), ('9', -0.23906793553945951), ('co', 0.17889581762548948), ('FOMO', 0.17816371816310961), ('our', 0.16223034436948144), ('addiction', 0.15582307139305418), ('https', -0.14618193818834138), ('playing', 0.13204607486577008), ('smartphone', 0.11208233840701091)]
5000/5000 [=======

1/1 [==============================] - 0s
Probability(positive) = 0.00220858
True class: depressed
[('anxiety', 0.34842250656717844), ('dial', -0.21092226531261402), ('natural', -0.19764211166803), ('down', 0.15385186288257355), ('before', -0.14943995178342673), ('ways', -0.12739208825360643), ('https', -0.12488254456254354), ('co', 0.12406641600265744), ('all', 0.080914740787355222), ('to', 0.068363652079817191)]
1/1 [==============================] - 0s
Probability(positive) = 0.000692897
True class: depressed
[('t', -0.057028103023994144), ('https', -0.056671803389459714), ('co', -0.024544803512866527), ('resistance', -0.0027952597686416), ('9JNK2M2900', -0.0025034192022543003), ('resist', -0.0020866753244195568)]
1/1 [==============================] - 0s
Probability(positive) = 0.999908
True class: depressed
[('depression', 0.44273645182890881), ('Depressed', 0.20147568672500002), ('Feels', -0.11006834176816026), ('her', -0.10354881687195497), ('letter', 0.087670672629381122), ('In

...

1/1 [==============================] - 0s
Probability(positive) = 1.0
True class: depressed
[('Need', 0.091656803301549419), ('Depression', 0.088995278622899313), ('Believing', 0.075076878484166096), ('Myths', 0.041278716912950528), ('8', 0.026389273619455023), ('https', -0.020056805801611548), ('co', 0.019265818003657155), ('Stop', -0.013855166166065091), ('vOx9Aciknn', 0.011286951560155162), ('We', 0.010666842533103999)]
1/1 [==============================] - 0s
Probability(positive) = 0.99998
True class: depressed
[('depression', 0.50948405766862392), ('like', -0.26032635705782353), ('see', 0.11952873490593263), ('breathing', 0.10868703657456595), ('drowning', 0.099972402288874204), ('everyone', -0.087024211894343617), ('can', -0.076491728238167481), ('except', 0.067890806991176542), ('RT', -0.055183160965490446), ('s', 0.054231289274451193)]
1/1 [==============================] - 0s
Probability(positive) = 1.0
True class: depressed
[('dead', 0.08020129649013108), ('anxiety', 0.0791

1/1 [==============================] - 0s
Probability(positive) = 0.0786381
True class: depressed
[('depression', 0.65672811904283468), ('like', -0.3140010762305056), ('https', -0.21616205175199948), ('t', -0.16668243415441192), ('what', 0.10696161792728028), ('co', -0.10144556464083906), ('does', -0.048086271341816013), ('look', -0.025142966117282256), ('TheMindBlowings', 0.02497381872385224), ('Y1z2QZIDwe', 0.018878592078830525)]
1/1 [==============================] - 0s
Probability(positive) = 0.999999
True class: depressed
[('depression', 0.90953203102095559), ('like', -0.073316142038583332), ('s', 0.046450990775577079), ('from', 0.032079437261075872), ('really', -0.030504629311231067), ('https', -0.029896727533907985), ('t', -0.028697123087894013), ('Here', -0.026915264538232099), ('co', -0.02159777475562779), ('RT', -0.019374593974475926)]
1/1 [==============================] - 0s
Probability(positive) = 0.991796
True class: depressed
[('Depression', 0.49272189789492749), ('Somet

1/1 [==============================] - 0s
Probability(positive) = 1.0
True class: depressed
[('depression', 0.046266549255442296), ('eats', 0.033880302624801954), ('worries', 0.031558306198736549), ('naps', 0.030371356644299803), ('sight', 0.02904045154676415), ('day', -0.027361064031164221), ('wcw', 0.022334923874299115), ('ur', -0.020310512194085337), ('im', 0.012999960244660859), ('it', 0.010084897797179195)]
5000/5000 [==============================] - 0s     
Test text: RT _Belize I know my depression is at it s peak when I don t even have a appetite after I smoke
1/1 [==============================] - 0s
Probability(positive) = 0.999994
True class: depressed
[('depression', 0.34627228533959858), ('smoke', 0.17796692956865778), ('appetite', 0.16773412753075947), ('RT', -0.058740853409123363), ('a', -0.054791259090657837), ('know', -0.040924681815767062), ('s', 0.034528801230196797), ('it', 0.030727918970156382), ('at', 0.027327773373886737), ('is', 0.014607323087843719)]
1/1 [====

1/1 [==============================] - 0s
Probability(positive) = 1.0
True class: depressed
[('depression', 0.060612459574339722), ('anxiety', 0.055834369991604689), ('judgment', 0.036628124145743048), ('decision', 0.035144875980306668), ('decline', 0.031073872836196587), ('continues', 0.024198277197901286), ('as', 0.021261489139191687), ('making', 0.019485964489605542), ('mental', -0.01660716678939874), ('cloud', 0.014159249394381004)]
1/1 [==============================] - 0s
Probability(positive) = 0.878857
True class: depressed
[('anxiety', 0.65813421829081364), ('level', 0.20374947887328965), ('para', 0.16394736829549209), ('t', -0.13054448881738845), ('https', -0.11293305597822131), ('co', -0.08399975745743167), ('how', -0.069376564075673219), ('to', 0.064774241994187437), ('RT', -0.064627947149724099), ('1', -0.022242369387103861)]
1/1 [==============================] - 0s
Probability(positive) = 1.0
True class: depressed
[('depression', 0.11131297736447408), ('other', 0.0689042

'\n# We choose a sample from test set\nidx = 36\ntestSample = xTest[idx]\nexp = explainer.explain_instance(xTest[idx], pipeline.predict_proba)\nprint("Test text: " + testSample)\nprint(\'Probability(positive) =\', pipeline.predict_proba([testSample])[0,1])\nprint(\'True class: %s\' % class_names[yTest[idx]])\n'

In [28]:
exp.as_list()

[('depression', 0.11557140709571376),
 ('ur', -0.10585002060517294),
 ('worries', 0.10181105259613035),
 ('naps', 0.089986345200396917),
 ('sight', 0.089942419412112021),
 ('eats', 0.087860466842257109),
 ('nothing', 0.057904040683819401),
 ('day', -0.039428682821041845),
 ('im', -0.036191305414680408),
 ('takes', 0.025772014321159761)]

In [29]:
exp.show_in_notebook(text=False)

### Chinese

In [72]:
#Read in the csv
chinDataDf = pd.read_csv("data_with_features/chin_cleaned_data_f.csv", encoding='UTF-8')
#Only take the text and sentiment columns
chinDataDf = chinDataDf[['text', 'depressed']]
#Cleaning
for index, row in chinDataDf.iterrows():
    #Preprocessing
    chinText, engText = tfExtractor.splitChinEng(row['text'])
    text = tfExtractor.chinPreprocessing(chinText)
    chinDataDf.set_value(index,'text',text)
#Convert data to numpy array
X = np.array(chinDataDf['text'].tolist())
Y = np.array(chinDataDf['depressed'].tolist())
#Convert -1 label to 0
i = 0
for label in Y:
    if(label == -1):
        Y[i] = 0
    i += 1
xString = []
for text in X:
    xString.append(' '.join(text))

C:\Users\richi\Anaconda3\envs\python35\lib\site-packages\ipykernel_launcher.py:10: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
  # Remove the CWD from sys.path while we load stuff.


In [73]:
xChinTrain, xChinTest, yChinTrain, yChinTest = train_test_split(xString, Y, test_size=0.2, shuffle=True, random_state=42, stratify=Y)

In [74]:
chinSequencer = TextsToSequences(num_words=vocabSize)
chinPadder = Padder(583)
maxLength = 583
chinSklearnRnn = KerasClassifier(build_fn=createRnnModel, epochs=20, batch_size=batchSize, verbose=1)

In [75]:
chinPreprocessPipeline = make_pipeline(chinSequencer, chinPadder)
chinPipeline = make_pipeline(chinSequencer, chinPadder, chinSklearnRnn)
chinPreprocessPipeline.fit(xChinTrain, yChinTrain)
chinPipeline.fit(xChinTrain, yChinTrain);
yPred = chinPipeline.predict(xChinTest)
yPredNorm = []
for p in yPred:
    if p > 0.5:
        yPredNorm.append(1)
    else:
        yPredNorm.append(0)
rnn_average_precision = average_precision_score(yChinTest, yPred)
rnn_recall_score = recall_score(yChinTest, yPred, average='binary')
rnn_accuracy_score = accuracy_score(yChinTest, yPredNorm)
print("Precision: " + str(rnn_average_precision))
print("Recall: " + str(rnn_recall_score))
print("Accuracy: " + str(rnn_accuracy_score))

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_9 (Embedding)      (None, 583, 128)          640000    
_________________________________________________________________
conv1d_9 (Conv1D)            (None, 583, 128)          49280     
_________________________________________________________________
max_pooling1d_9 (MaxPooling1 (None, 291, 128)          0         
_________________________________________________________________
lstm_8 (LSTM)                (None, 500)               1258000   
_________________________________________________________________
dense_8 (Dense)              (None, 1)                 501       
Total params: 1,947,781
Trainable params: 1,947,781
Non-trainable params: 0
_________________________________________________________________
None
Epoch 1/20
643/643 [==============================] - 60s 93ms/step - loss: 0.6470 - acc: 0.6267
Epoch 2/20
643/643 [==========

In [20]:
class_names = ['not_depressed', 'depressed']
explainer = LimeTextExplainer(class_names=class_names)
testText = "我們是快樂的好兒童 我們天天一起歌唱 我們在學習 我們在成長 我們是春天的花 我們是未來的主人翁 我們是社會的棟樑 校長你好嗎？ 老師你好嗎？我們天天問侯你"
testTextReady = ' '.join(tfExtractor.chinPreprocessing(testText))
exp = explainer.explain_instance(testTextReady, chinPipeline.predict_proba)
exp.show_in_notebook(text=True)
print(pred)

C:\Users\richi\Anaconda3\envs\py3.5\lib\re.py:203: FutureWarning: split() requires a non-empty pattern match.
  return _compile(pattern, flags).split(string, maxsplit)


5000/5000 [==============================] - 21s    


[[0]]


In [92]:
#Save preprocessing pipeline
joblib.dump(chinPreprocessPipeline, "saved_model/chinPreprocessPipeline.pkl")
print("pipeline saved")
chinPreprocessPipeline = joblib.load('saved_model/chinPreprocessPipeline.pkl')
print("pipeline loaded")

pipeline saved
pipeline loaded


### Visualization

In [62]:
# We choose a sample from test set
class_names = ['not_depressed', 'depressed']
explainer = LimeTextExplainer(class_names=class_names)
i = 0
j = 0
for testData in xChinTest:
    if(yChinTest[i] == 1):
        exp = explainer.explain_instance(testData, chinPipeline.predict_proba)
        print("Test text: " + testData)
        print('Probability(positive) =', chinPipeline.predict_proba([testData])[0,1])
        print('True class: %s' % class_names[yChinTest[i]])
        print(exp.as_list())
        exp.save_to_file("chin_test_data_diagrams/tdd_" + str(j) + ".html")
        j += 1
        #exp.show_in_notebook(text=True)
    i += 1
"""
testSample = xChinTest[idx]
class_names = ['not_depressed', 'depressed']
explainer = LimeTextExplainer(class_names=class_names)
exp = explainer.explain_instance(xChinTest[idx], pipeline.predict_proba)
print("Test text: " + testSample)
print('Probability(positive) =', pipeline.predict_proba([testSample])[0,1])
print('True class: %s' % class_names[yChinTest[idx]])
"""

C:\Users\richi\Anaconda3\envs\py3.5\lib\re.py:203: FutureWarning: split() requires a non-empty pattern match.
  return _compile(pattern, flags).split(string, maxsplit)


1/1 [==============================] - 0s
Probability(positive) = 0.999936
True class: depressed
[('我', 0.12151567531570805), ('了', 0.054157507288166082), ('以为', -0.047124767217291121), ('怎么办', 0.044859224199957352), ('会', 0.038956961728795626), ('上学', 0.037671597845950262), ('时候', 0.036754960231068008), ('比', 0.031599897608839245), ('这些', 0.031256109155036425), ('想到', 0.030404810762837322)]
1/1 [==============================] - 0s
Probability(positive) = 0.970823
True class: depressed
[('我', 0.43860763788413476), ('可惜', -0.12190028145859312), ('爱', 0.087045500635388004), ('吗', 0.086009822535868294), ('还', 0.06077766680994437), ('不会', 0.058741413569016875), ('了', 0.050514156468654869), ('已经', 0.041582493738676785), ('很多', 0.033033515452862976), ('去', 0.02581389620403067)]
1/1 [==============================] - 0s
Probability(positive) = 0.999808
True class: depressed
[('我', 0.32314317041522406), ('死亡', 0.13464795163351795), ('或', -0.093920973941895108), ('说话', -0.088210009855786892), 

1/1 [==============================] - 0s
Probability(positive) = 0.999979
True class: depressed
[('我', 0.49926031183236519), ('现在', 0.13277110227450828), ('心', 0.1048117729308347), ('这些', 0.10168294897137255), ('真的', 0.09008829580417986), ('仲有', -0.088933937113751513), ('正常', -0.088394117413218273), ('几', -0.068552789548383092), ('应该', 0.068468294983299829), ('照顾', -0.065935371390316286)]
1/1 [==============================] - 0s
Probability(positive) = 0.0570548
True class: depressed
[('就要', -0.26190680112667047), ('但系', 0.18705288688617977), ('书', -0.18033778317571056), ('值得', -0.13706269230664533), ('功课', -0.12420234580901014), ('辛苦', 0.11953548655478326), ('睇', 0.11526067771842335), ('唉', -0.10772532368906226), ('小', -0.095777992157676933), ('好', -0.064597318206156731)]
5000/5000 [==============================] - 0s     
Test text: 不 知道 实在 唔 开心 近来 实在 太多 人同 我 讲话 我 就 来 仲 未有 一份 稳定 既 工作 又 唔 肯 养家 问 我 点算 依个 问题 令 我 太 困扰 好大 压力 我 自己 面对 都 好 唔 开心 都 唔 知 可以 点算 我 都 很 担心 自己 徐了 果份工 根本 唔 知 自己 可以 

1/1 [==============================] - 0s
Probability(positive) = 0.999999
True class: depressed
[('我', 0.041045027585529831), ('真的', 0.035331826079230237), ('想', 0.035082620055622224), ('会', 0.021383069353807016), ('自杀', 0.019697383886747154), ('了', 0.01815930455678768), ('但', -0.010830916453691214), ('们', -0.010597862187969981), ('找', -0.0091168686410435917), ('跟', -0.0054026912853075339)]
5000/5000 [==============================] - 0s     
Test text: 月 日 人生 苦短 都 吾 知 点解 活得 咁 辛苦 理想 是 什么 没 理想 活着 意义 何在 好 辛苦 到底 应该 要点 先 可以 好转 呢 下星期 要 倾 破产 了 点样 吾 想 感觉 也 没用 生命 在 消散 中
1/1 [==============================] - 0s
Probability(positive) = 0.0228283
True class: depressed
[('下星期', -0.43389672598249224), ('想', 0.23653920744002346), ('了', 0.21541698202125717), ('吾', -0.19886195476060306), ('点样', -0.18358742344087342), ('倾', -0.15117930073230909), ('辛苦', 0.15085556782568077), ('要', -0.14612009580942975), ('感觉', 0.11490546065324972), ('理想', -0.079517090402007912)]
1/1 [==============================] -

1/1 [==============================] - 0s
Probability(positive) = 7.21613e-05
True class: depressed
[('上', -0.10053373046553195), ('就是', -0.085613451672841442), ('失去', -0.074564545485580225), ('但', -0.058685227934259433), ('觉得', -0.047330022209361777), ('每个', -0.042206274422720805), ('怎会', -0.04191566553207534), ('从前', -0.040128176769425872), ('生命', 0.031986581777378335), ('自杀', 0.029900978131876418)]
1/1 [==============================] - 0s
Probability(positive) = 0.944487
True class: depressed
[('只不过', -0.38866075739324102), ('现在', 0.37810206664296059), ('我', 0.30181168096216465), ('会', 0.13728828006758526), ('真的', 0.12874152085002621), ('一个', 0.12719976856163875), ('神', -0.1133631995106917), ('我们', 0.077614062198325451), ('礼物', -0.058167546755779051), ('考验', 0.046446503827645175)]
1/1 [==============================] - 0s
Probability(positive) = 0.999883
True class: depressed
[('我', 0.54863245808841332), ('佢', 0.19256027206724413), ('我们', 0.073200586738838766), ('辛苦', 0.06589392147

1/1 [==============================] - 0s
Probability(positive) = 0.999511
True class: depressed
[('我', 0.35861903577562804), ('不到', -0.20597094263806853), ('一个', 0.19549049793494011), ('安全', -0.11801337850223129), ('了', 0.10173134672123917), ('的', 0.10167531812227605), ('累', 0.09744342222886053), ('小', 0.093376934838323697), ('这样', 0.088012222088226358), ('找', -0.069786962530427377)]
1/1 [==============================] - 0s
Probability(positive) = 0.00568006
True class: depressed
[('心情', -0.19596096584341896), ('想', 0.074313378064023633), ('死', 0.07022032019627901), ('很烦', 0.01411829816484335), ('极差', 0.012005941311880649), ('烦到', 0.0086222686162653692)]
1/1 [==============================] - 0s
Probability(positive) = 0.018212
True class: depressed
[('我', 0.52423803434037342), ('天父', -0.22215150266797684), ('经历', -0.18842826257126566), ('那些', -0.1690343378557688), ('生活', -0.15321275582867158), ('想起', -0.151571269590762), ('要', -0.1318893879219348), ('真是', -0.12037898323257987), ('过'

1/1 [==============================] - 0s
Probability(positive) = 0.999999
True class: depressed
[('我', 0.7042112227252173), ('帮', -0.24029887423326191), ('等待', -0.072528929109461043), ('结束', 0.044208792046837093), ('真的', 0.043339337398869339), ('在', 0.033375512042600156), ('好', 0.025726895461171746), ('生命', 0.023861885716125866), ('辛苦', 0.022288028355735418), ('你', -0.011150235514285241)]
1/1 [==============================] - 0s
Probability(positive) = 0.997653
True class: depressed
[('我', 0.15854215510005643), ('这些', 0.081789621683878946), ('想起', -0.081089120738132625), ('一次', 0.071393804768814614), ('了', 0.039558319943620981), ('唉', -0.036137089412512181), ('心', 0.036063872931054147), ('真的', 0.035707808205686635), ('累', 0.032727763303483724), ('又', -0.020820449958662859)]


'\ntestSample = xChinTest[idx]\nclass_names = [\'not_depressed\', \'depressed\']\nexplainer = LimeTextExplainer(class_names=class_names)\nexp = explainer.explain_instance(xChinTest[idx], pipeline.predict_proba)\nprint("Test text: " + testSample)\nprint(\'Probability(positive) =\', pipeline.predict_proba([testSample])[0,1])\nprint(\'True class: %s\' % class_names[yChinTest[idx]])\n'

In [43]:
exp.as_list()

[('我', 0.3716717123051429),
 ('可惜', -0.1176358090459725),
 ('还', 0.10698479251437991),
 ('爱', 0.087363210505954414),
 ('不会', 0.069602280889600285),
 ('吗', 0.065900828937778322),
 ('了', 0.04525767842225692),
 ('也', 0.038836387536309733),
 ('知道', -0.03627826972110651),
 ('记得', -0.035239830823205212)]

In [46]:
exp.show_in_notebook(text=True)